## CNU 공공데이터 open API 데이터 가져오기 예제

다음의 데이터를 가져옵니다.
-   충남대학교 게시판 번호
-   충남대학교 게시판 번호 별 내용

In [ ]:
pip install requests pandas

In [7]:
import requests, json
from datetime import datetime

"""
    credential.json에 요청 URL, API KEY 등을 입력하여
    file open으로 불러오는 방식을 사용합니다.
"""

with open('credential.json','r') as file:
    credentials = json.load(file)

print(credentials)

API_KEY = credentials["API_KEY"] # CNU API KEY
POST_NUM_URL = credentials["POST_NUM_URL"] # 게시판 목록 불러오기
POST_CONTENT_URL = credentials["POST_CONTENT_URL"] # 게시판 내용 불러오기

{'POST_NUM_URL': 'https://api.cnu.ac.kr/svc/offcam/pub/cmsBoard', 'POST_CONTENT_URL': 'https://api.cnu.ac.kr/svc/offcam/pub/homepageboardContents', 'API_KEY': '62E7DD21612148E0B5766DDEE9110FF06A5E0311'}


In [8]:
"""
    게시판 목록 불러오기 API를 사용하여 데이터를 가져옵니다.
"""

request_body = requests.post(url = POST_NUM_URL, params={"AUTH_KEY" : API_KEY})

In [ ]:
"""
    게시판 목록 불러오기 API를 사용하여 데이터를 가져온 이후,
    게시판 내용 불러오기 API를 사용하여 번호에 해당하는 데이터를 가져옵니다.
"""

results = request_body.json()["RESULT"] # 가져온 데이터의 결과
data_to_save = list()

for idx, result in enumerate(results):
    

    post_num_data = {
        "site_name" : result["site_nm"],
        "board_number" : result["board_no"],
        "board_name" : result["board_nm"]
    }
    
    print(f"Processing for post_num {post_num_data.get('board_number')}.. {idx}/{len(results)}")

    if post_num_data["board_number"] == 1170:
        print(f"too many datas in {post_num_data.get('board_number')}")
        continue

    content_request_body = requests.post(url = POST_CONTENT_URL, 
                                 params={
                                     "AUTH_KEY" : API_KEY,
                                     "P_board_no":post_num_data["board_number"]
                                     })
        
    # content_results = content_request_body.json()["RESULT"]
    content_results_string = content_request_body.text
    cleaned_string = ''.join(char for char in content_results_string if (31 < ord(char) < 127) or (char in '\r\n\t') or ('\uAC00' <= char <= '\uD7A3'))
    content_results = json.loads(cleaned_string).get('RESULT')

    if content_results is None:
        print(content_results_string)
        continue

    """
        해당 게시판 번호를 통해 게시판 내용 불러오기
        예) 컴퓨터 융합학부 학사공지 게시판 번호 -> 컴융 학사 공지에 대한 모든 게시글 불러옴
    """
    for content_idx, content_result in enumerate(content_results):
        print(f"Processing for post_content_data.. {content_idx}/{len(content_results)}")
        post_num_data = {
            "site_name" : content_result["board_nm"],
            "article_number" : content_result["article_no"],
            "article_title" : content_result["article_title"],
            "article_text" : content_result["article_text"],
            "writer_name" : content_result["writer_nm"],
            "click_count" : content_result["click_cnt"],
            "update_date" : content_result["update_dt"],
        }

        # 밀리초 단위의 타임스탬프
        timestamp_ms = post_num_data["update_date"]["time"]

        # 밀리초를 초로 변환
        timestamp_s = timestamp_ms / 1000

        # 타임스탬프를 datetime 객체로 변환
        datetime_obj = datetime.fromtimestamp(timestamp_s)

        # YYYY-MM-DD hh:mm:ss 형식으로 변환하여 반환
        post_num_data["update_date"] = datetime_obj.strftime('%Y-%m-%d %H:%M:%S')

        data_to_save.append(post_num_data)

Processing for post_num 87.. 0/534
Processing for post_content_data.. 0/90
Processing for post_content_data.. 1/90
Processing for post_content_data.. 2/90
Processing for post_content_data.. 3/90
Processing for post_content_data.. 4/90
Processing for post_content_data.. 5/90
Processing for post_content_data.. 6/90
Processing for post_content_data.. 7/90
Processing for post_content_data.. 8/90
Processing for post_content_data.. 9/90
Processing for post_content_data.. 10/90
Processing for post_content_data.. 11/90
Processing for post_content_data.. 12/90
Processing for post_content_data.. 13/90
Processing for post_content_data.. 14/90
Processing for post_content_data.. 15/90
Processing for post_content_data.. 16/90
Processing for post_content_data.. 17/90
Processing for post_content_data.. 18/90
Processing for post_content_data.. 19/90
Processing for post_content_data.. 20/90
Processing for post_content_data.. 21/90
Processing for post_content_data.. 22/90
Processing for post_content_data

In [ ]:
import pandas as pd

"""
    pandas를 통해 파이썬 리스트를 json 파일로 변환하고, csv파일로 저장한다. 
"""

df = pd.json_normalize(data_to_save)
print(df)

written_data = df.to_csv('cnu_post_data.csv', index=True)